In [1]:
import pandas as pd 

file =  pd.read_csv('text.csv')

In [2]:
file =  file.drop(columns={'Unnamed: 0','Unnamed: 0.1'})

In [3]:
sample =  file['review'][3]

In [4]:
sample  =  sample.lower()

In [5]:
import re 
sample  =  re.sub('[^\w\s]','',sample)

<>:2: SyntaxWarning: invalid escape sequence '\w'
<>:2: SyntaxWarning: invalid escape sequence '\w'
C:\Users\mahmoud.sadiek\AppData\Local\Temp\ipykernel_38844\2807955736.py:2: SyntaxWarning: invalid escape sequence '\w'
  sample  =  re.sub('[^\w\s]','',sample)


In [6]:
import nltk
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize

stop_words =  stopwords.words('english')

In [7]:
tokens = word_tokenize(sample)

In [8]:
token_text =  [word for word in tokens if word not in stop_words]

In [9]:
from nltk.stem import PorterStemmer

In [10]:
steemer  =  PorterStemmer()

In [11]:
clean_text =  [steemer.stem(word) for word in token_text  ]

In [12]:
clean_text

['basic',
 'there',
 'famili',
 'littl',
 'boy',
 'jake',
 'think',
 'there',
 'zombi',
 'closet',
 'parent',
 'fight',
 'timebr',
 'br',
 'movi',
 'slower',
 'soap',
 'opera',
 'suddenli',
 'jake',
 'decid',
 'becom',
 'rambo',
 'kill',
 'zombiebr',
 'br',
 'ok',
 'first',
 'your',
 'go',
 'make',
 'film',
 'must',
 'decid',
 'thriller',
 'drama',
 'drama',
 'movi',
 'watchabl',
 'parent',
 'divorc',
 'argu',
 'like',
 'real',
 'life',
 'jake',
 'closet',
 'total',
 'ruin',
 'film',
 'expect',
 'see',
 'boogeyman',
 'similar',
 'movi',
 'instead',
 'watch',
 'drama',
 'meaningless',
 'thriller',
 'spotsbr',
 'br',
 '3',
 '10',
 'well',
 'play',
 'parent',
 'descent',
 'dialog',
 'shot',
 'jake',
 'ignor']

In [17]:
def clean_text(text):
    text =  text.lower()
    text =  re.sub(r'[^\w\s]','',text)
    text = re.sub(r'[0-9]','',text)
    tokens  =  word_tokenize(text)
    token_text =  [word for word in tokens if word not in stop_words]
    clean_text =  [steemer.stem(word) for word in token_text  ]
    clean_text  = ' '.join(clean_text)
    return clean_text
    
    

In [18]:
file['clean_review'] =  file['review'].apply(clean_text)

In [21]:
from sklearn.feature_extraction.text import TfidfVectorizer
victorizer =  TfidfVectorizer(max_features=2500)

In [23]:
file2 =  victorizer.fit_transform(file['clean_review'])

In [26]:
df =  pd.DataFrame(file2.toarray() , columns=victorizer.get_feature_names_out())

In [28]:
from sklearn.model_selection import train_test_split
from sklearn.ensemble import RandomForestClassifier
forest =  RandomForestClassifier()

In [30]:
df['judge'] =  file['sentiment']

In [31]:
x= df.drop(columns={'judge'})
y=  df['judge']

In [32]:
xtrain ,xtest ,ytrain , ytest =  train_test_split(x,y,train_size=.80,random_state=42)
forest.fit(xtrain,ytrain)

RandomForestClassifier()

In [33]:
ypredict  =  forest.predict(xtest)


In [34]:
from sklearn.metrics import accuracy_score,classification_report

In [36]:
accuracy_score(ytest,ypredict)

0.8497

In [37]:
print(classification_report(ytest,ypredict))

              precision    recall  f1-score   support

    negative       0.84      0.86      0.85      4961
    positive       0.86      0.84      0.85      5039

    accuracy                           0.85     10000
   macro avg       0.85      0.85      0.85     10000
weighted avg       0.85      0.85      0.85     10000



# Unsupervised

In [44]:
from sklearn.cluster import KMeans
custer_model =  KMeans(n_clusters=2)

In [45]:
cluster_classify = custer_model.fit_predict(df.drop(columns={'judge'}))

In [46]:
df['cluster_model'] = cluster_classify

In [47]:
df[['judge','cluster_model']]

judge  cluster_model
0      positive              0
1      positive              1
2      positive              1
3      negative              1
4      positive              1
...         ...            ...
49995  positive              0
49996  negative              0
49997  negative              1
49998  negative              1
49999  negative              0

[50000 rows x 2 columns]

In [48]:
from sklearn.decomposition import PCA
pca_encoder =  PCA(random_state=42,n_components=2)

In [49]:
pcadata =  pca_encoder.fit_transform(df.drop(columns={'judge','cluster_model'}))

In [52]:
pcadata = pd.DataFrame(pcadata)

In [54]:
pcadata['judge'] =  df['judge']
pcadata['cluster'] =  df['cluster_model']


In [57]:
pcadata

0         1     judge  cluster
0     -0.052013  0.008361  positive        0
1     -0.098282  0.126310  positive        1
2     -0.033676 -0.015017  positive        1
3      0.021555  0.060883  negative        1
4     -0.077043  0.104759  positive        1
...         ...       ...       ...      ...
49995  0.210961  0.056240  positive        0
49996  0.040017  0.025553  negative        0
49997 -0.016352 -0.017076  negative        1
49998 -0.059892 -0.072079  negative        1
49999  0.364675  0.003304  negative        0

[50000 rows x 4 columns]

In [62]:
import plotly.express as px 
fig =  px.scatter(  data_frame=pcadata , x=0 , y=1 ,color='judge'  )
fig.show()

In [65]:
fig =  px.scatter(  data_frame =pcadata , x=0 , y=1 ,color= pcadata['cluster'].astype('str')  )
fig.show()